# Evolutionary Computation Assignment 3

- Krzysztof Szala 144571
- Vadym Repetskyi 155610


In [1]:
from utils import TspInstance, random_solution, weighted_regret
import numpy as np
import pandas as pd
import itertools

In [2]:
def intra_route_move(tsp, solution, intra_type, steepest):
    indexes = range(len(solution))
    neighborhood = [(u, v) for u in indexes for v in indexes if u != v]
    np.random.shuffle(neighborhood)

    min_cost = 0
    selected_a = selected_b = None

    for index_a, index_b in neighborhood:
        # we can draw first edge with any node, but second have to start from not node_a and not node_a+1 or node_a-1
        if intra_type != "nodes" and abs(index_a - index_b) == 1:
            continue

        a = solution[index_a]
        b = solution[index_b]

        a_prev = solution[index_a - 1]
        b_prev = solution[index_b - 1]

        a_next = solution[(index_a + 1) % len(solution)]
        b_next = solution[(index_b + 1) % len(solution)]

        if intra_type == "nodes":
            cost_change = (
                tsp.distance_matrix[a_prev, b]
                + tsp.distance_matrix[b, a_next]
                + tsp.distance_matrix[b_prev, a]
                + tsp.distance_matrix[a, b_next]
                - tsp.distance_matrix[a_prev, a]
                - tsp.distance_matrix[a, a_next]
                - tsp.distance_matrix[b_prev, b]
                - tsp.distance_matrix[b, b_next]
            )
        else:
            cost_change = (
                tsp.distance_matrix[a, b]
                + tsp.distance_matrix[a_next, b_next]
                + -tsp.distance_matrix[a, a_next]
                - tsp.distance_matrix[b, b_next]
            )

        if cost_change < min_cost:
            min_cost = cost_change
            selected_a = index_a
            selected_b = index_b

            if not steepest:
                break

    if selected_a is not None:
        if intra_type == "nodes":
            # Just swap the two nodes

            solution[selected_a], solution[selected_b] = (
                solution[selected_b],
                solution[selected_a],
            )
        else:
            # node_a stays at the same position
            # node_a+1 become node_b
            # node_b become node_a+1
            # node b+1 stays at the same position

            solution[(selected_a + 1) % len(solution)], solution[selected_b] = (
                solution[selected_b],
                solution[(selected_a + 1) % len(solution)],
            )

    return solution, min_cost


def inter_route_move(tsp, solution, steepest):
    possible_unselect = set(solution)
    possible_select = set(range(tsp.size)) - possible_unselect
    neighborhood = list(itertools.product(possible_unselect, possible_select))
    np.random.shuffle(neighborhood)

    min_cost = 0
    to_unselect = to_select = None

    for test_unselect, test_select in neighborhood:
        insert_index = np.where(solution == test_unselect)[0][0]

        prev = solution[insert_index - 1]
        next = solution[(insert_index + 1) % len(solution)]

        cost_change = (
            tsp.node_costs[test_select]
            + tsp.distance_matrix[prev, test_select]
            + tsp.distance_matrix[test_select, next]
            - tsp.node_costs[test_unselect]
            - tsp.distance_matrix[prev, test_unselect]
            - tsp.distance_matrix[test_unselect, next]
        )

        if cost_change < min_cost:
            min_cost = cost_change
            to_unselect = test_unselect
            to_select = test_select

            if not steepest:
                break

    if to_unselect is not None:
        solution[np.where(solution == to_unselect)] = to_select

    return solution, min_cost

## Local Search

### Greedy

1. Choose arbitrarily starting node and generate random/weighted(best heuristic so far) solution
2. Check each move if solution with it it's better
3. Finish, wehn you check all of them and none of them give us better solution.

Randomly selecting solution

1. Randomly choose if inter/intra route move
2. Randomly look for next solution, remembering already visited solutions

### Steepest

TODO


In [3]:
def local_search(
    tsp: TspInstance,
    start_node: int,
    initial_solution_getter: callable,
    intra_type: str,
    steepest: bool,
):
    solution = initial_solution_getter(tsp, start_node)

    previous = set()

    while True:
        previous.add(str(solution))
        if np.random.rand() < 0.5:
            solution, cost_change = inter_route_move(tsp, solution, steepest)

            if cost_change == 0:
                solution, cost_change = intra_route_move(
                    tsp, solution, intra_type, steepest
                )
        else:
            solution, cost_change = intra_route_move(
                tsp, solution, intra_type, steepest
            )

            if cost_change == 0:
                solution, cost_change = inter_route_move(tsp, solution, steepest)

        if cost_change == 0:
            break

        if str(solution) in previous:
            print("Already seen", solution, " in ", previous)
            break

    return solution

## Experiments

In [4]:
columns = []
experiments = []

for instance in (TspInstance("TSPA.csv"), TspInstance("TSPB.csv")):
    for intra_type in ("nodes", "edges"):
        for steepest in (True, False):
            for initial_solution_getter in (random_solution, weighted_regret):
                column = f"{instance.file_path[3]} {"steepest" if steepest else "greedy"} {intra_type} {initial_solution_getter.__name__.split("_")[0]}".upper()
                print(column)
                columns.append(column)
                experiments.append(
                    instance.run_experiments(
                        local_search, initial_solution_getter, intra_type, steepest
                    )
                )

A STEEPEST NODES RANDOM
001/200 Already seen [ 90 106  98   8 161  42 108 194 182  55  44  13  27 151  94 116 190 184
  28 160  22  97  75   1  96  59  63 155  16  45 135 140  83  25 145 169
  31 175  74 179  43 181 192 114 180  70 148 176 197  68 139 137  71  91
 100 170  67  50  81 157  78  85 101  26  57  48 123 173  33 143 131 159
 193  36  41  89 117  46 115   4  35 150  49  65 105 166 111  12  52   3
  62  79  64  95 113  56 171 120 167 124]  in  {'[124 106  98   8 161  42 108 194  55 182 116  13  27 151  94 190  44  73\n  28 160  22  97  75   1  96 134  63 155  16  45 135 140  83  25 145 169\n  31 175  74 179  43 181 192 114  88  70 148  17 197  68 147 137  71  91\n 100 170  67  50  81 157  78  85  47  26  57  48 173  20  33 143 131 159\n 193  36  89  41  99 119   4 117  35 150  49  58 105 166 111  12  52   3\n  84  79  64 113  95  56 171 120 167  90]', '[ 90 106  98   8 161  42 108 194 182  55  44  13  27 151  94 116 190 184\n  28 160  22  97  75   1  96  59  63 155  16  45 135

In [6]:
pd.DataFrame(
    np.array(tuple(map(lambda x: x[:-1], experiments))).T,
    columns=columns,
    index=(
        "min_cost",
        "max_cost",
        "average_cost",
        "min_time",
        "max_time",
        "average_time",
    ),
)

A STEEPEST NODES RANDOM  A STEEPEST NODES WEIGHTED  \
min_cost                184940.000000              136761.000000   
max_cost                184940.000000              136761.000000   
average_cost               924.700000                 683.805000   
min_time                     1.879614                   1.493310   
max_time                     1.879614                   1.493310   
average_time                 0.009398                   0.007467   

              A GREEDY NODES RANDOM  A GREEDY NODES WEIGHTED  \
min_cost               83210.000000            103751.000000   
max_cost               83210.000000            103751.000000   
average_cost             416.050000               518.755000   
min_time                  12.463411                 2.638659   
max_time                  12.463411                 2.638659   
average_time               0.062317                 0.013193   

              A STEEPEST EDGES RANDOM  A STEEPEST EDGES WEIGHTED  \
min_cost                205916.000000              107708.000000   
max_cost                205916.000000              107708.000000   
average_cost              1029.580000                 538.540000   
min_time                     0.484832                   3.695656   
max_time                     0.484832                   3.695656   
average_time                 0.002424                   0.018478   

              A GREEDY EDGES RANDOM  A GREEDY EDGES WEIGHTED  \
min_cost              104410.000000            117817.000000   
max_cost              104410.000000            117817.000000   
average_cost             522.050000               589.085000   
min_time                  11.483304                16.551549   
max_time                  11.483304                16.551549   
average_time               0.057417                 0.082758   

              B STEEPEST NODES RANDOM  B STEEPEST NODES WEIGHTED  \
min_cost                125925.000000               80895.000000   
max_cost                125925.000000               80895.000000   
average_cost               629.625000                 404.475000   
min_time                     2.305582                   2.425818   
max_time                     2.305582                   2.425818   
average_time                 0.011528                   0.012129   

              B GREEDY NODES RANDOM  B GREEDY NODES WEIGHTED  \
min_cost               61735.000000             56905.000000   
max_cost               61735.000000             56905.000000   
average_cost             308.675000               284.525000   
min_time                   5.122848                 4.565222   
max_time                   5.122848                 4.565222   
average_time               0.025614                 0.022826   

              B STEEPEST EDGES RANDOM  B STEEPEST EDGES WEIGHTED  \
min_cost                144710.000000               89313.000000   
max_cost                144710.000000               89313.000000   
average_cost               723.550000                 446.565000   
min_time                     1.472532                   3.413996   
max_time                     1.472532                   3.413996   
average_time                 0.007363                   0.017070   

              B GREEDY EDGES RANDOM  B GREEDY EDGES WEIGHTED  
min_cost              112413.000000            107642.000000  
max_cost              112413.000000            107642.000000  
average_cost             562.065000               538.210000  
min_time                   1.616812                24.394486  
max_time                   1.616812                24.394486  
average_time               0.008084                 0.121972